# Verify the combined data

EDA to make sure the script within `GetPlayTimestamps.ipynb` worked correctly

In [161]:
import pandas as pd
import numpy as np
from datetime import timedelta

import bokeh
from bokeh.plotting import show, output_notebook
from bokeh.plotting import figure, show, output_file
from bokeh.palettes import brewer, Category20
from bokeh.models import DatetimeTickFormatter
from bokeh.models import HoverTool

output_notebook()

colors = brewer['Paired']

%matplotlib inline

Loading BokehJS ...

In [221]:
game = 'Eagles_vs_Panthers__2017-10-12'
df = pd.read_pickle('../../data/Clean_Game_Data/{}_comment_sentiment.pickle'.format(game))
df['winPercentageScaled'] = (df['homeWinPercentage'] - 0.5) * 2
df_filtered = df.loc[df['comment_created_utc_datetime'] < df['comment_created_utc_datetime'].min() + timedelta(hours=5)]
df_small = df_filtered[['text',
                        'comment_created_utc_datetime',
                        'winPercentageScaled',
                        'comment_body',
                        'author_flair',
                        'vader_compound']]

# Create dataframes for each comment type
home_team_comments = df_filtered.loc[df_filtered['author_flair'] == df_filtered['home_team'].loc[1]].copy()
away_team_comments = df_filtered.loc[df_filtered['author_flair'] == df_filtered['away_team'].loc[1]].copy()
other_comments = df_filtered.loc[(df_filtered['author_flair'] != df_filtered['away_team'].loc[1]) &
                        (df_filtered['author_flair'] != df_filtered['home_team'].loc[1])].copy()

# Create Bokeh Figure
p = figure(plot_height=500,
           plot_width=1000,
           sizing_mode='scale_width',
           x_axis_type="datetime",
           tools=['xwheel_zoom', 'xpan', 'reset', 'xbox_zoom', 'save'],           
           title="Game Analysis {}".format(game),
           y_range = (-1,1))

# Add Lines
winpct = p.line(x='comment_created_utc_datetime',
                y='winPercentageScaled',
                source=df_small,
                color=Category20[10][0])

# Win Percentage Line
# p.line(x=df_filtered['comment_created_utc_datetime'],
#        y=df_filtered['vader_compound'],
#        legend='Vader Sentiment All',
#        color=brewer['Dark2'][8][1])

# Comment Sentiment Lines
# p.line(x=home_team_comments['comment_created_utc_datetime'],
#        y=home_team_comments['vader_compound'],
#        legend='Vader Sentiment Home Team',
#        color=brewer['Dark2'][8][2])
# p.line(x=away_team_comments['comment_created_utc_datetime'],
#        y=away_team_comments['vader_compound'],
#        legend='Vader Sentiment Away Team',
#        color=brewer['Dark2'][8][3])
# p.line(x=other_comments['comment_created_utc_datetime'],
#        y=other_comments['vader_compound'],
#        legend='Vader Sentiment Others',
#        color=brewer['Dark2'][8][4])

# Add Rolling Sentiment

window_home = round(len(home_team_comments) / 20)
window_away = round(len(away_team_comments) / 20)
window_other = round(len(other_comments) / 20)

home_team_comments['vader_rolling'] = home_team_comments['vader_compound'].rolling(window=window_home).mean(center=True) * 4
away_team_comments['vader_rolling'] = away_team_comments['vader_compound'].rolling(window=window_away).mean(center=True) * 4
other_comments['vader_rolling'] = other_comments['vader_compound'].rolling(window=window_other).mean(center=True) * 4

p.line(x=home_team_comments['comment_created_utc_datetime'],
       y=home_team_comments['vader_rolling'],
       legend='Vader Sentiment {} Fans Rolling'.format(df_filtered['home_team'].loc[1]),
       color=Category20[10][2])
p.line(x=away_team_comments['comment_created_utc_datetime'],
       y=away_team_comments['vader_rolling'],
       legend='Vader Sentiment {} Fans Rolling'.format(df_filtered['away_team'].loc[1]),
       color=Category20[10][4])
p.line(x=other_comments['comment_created_utc_datetime'],
       y=other_comments['vader_rolling'],
       legend='Vader Sentiment Others Rolling',
       color=Category20[10][6])

# Create Hovertool
my_hover = HoverTool()
my_hover.tooltips = [
    ("Datetime", '@comment_created_utc_datetime{%F}'),
    ("winPercentageScaled", "@winPercentageScaled"),
    ("Last Play","@text"),
    ("Comment","@comment_body"),
    ("Comment Author Flair", "@author_flair"),
    ("Comment Vader Sentiment", "@vader_compound")]
my_hover.formatters = {"Datetime": "datetime"}
my_hover.renderers = [winpct]
my_hover.mode = 'vline'
p.add_tools(my_hover)

# Make line hide when clicked in legend
p.legend.click_policy = "hide"

# Show the Plot
show(p)

In [216]:
'Bears_vs_Packers__2017-09-28'

'Bears_vs_Packers__2017-09-28'